# 1. File description 

This file is meant to clean and tranform the data already existing to a format that will be used for labelling. Some EDA and feature engineering will be done here but as the data is not labelled, most of it will be done after the labelling.

## 2.1 Modules and UDFs

In [74]:
import src.viz as sv


# Data manipulation
import sqlite3
import pandas as pd
import numpy as np
from scipy.stats import kurtosis, skew

# Data vizualisation
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.io as pio

# For charging bars for for loops and pd.Series.apply()
from tqdm.auto import tqdm
tqdm.pandas()

# To control time
from datetime import datetime, timedelta

# To manupulate emojis
import demoji

# To retrive domain from url 
from urllib.parse import urlparse

# To move files around
import shutil

### Setting notebook preferences
Setting pandas to not limit the number of displayed columns and open database

In [75]:
pd.set_option("display.max_columns", None)
pio.templates.default = "plotly_dark"

# Creating SQL database to store all the data for the project
database = "data/main_database.sqlite"
con = sqlite3.connect(database)

In [76]:
query = '''
select 
    * 
from sqlite_master'''

df_sqlite_master = pd.read_sql_query('select * from sqlite_master', con)
for tbl in df_sqlite_master['tbl_name']:
    print(tbl, pd.read_sql_query(f'select * from {tbl}', con).shape)

comments (134465, 12)
last_12_posts (363408, 9)
post_ids (7831, 2)
photos (467299, 3)
users (86343, 65)


Now, each table is going to be cleaned and put in a nice format

### 1. Comments

The goal is to clean the table, and output it in a clean and organized table

In [77]:
query = '''
select 
    * 
from comments
'''

df_comments = pd.read_sql_query(query, con)
df_comments.query('username in page').head()

page       postid  \
28769   meme.ig  CYqmMFalyy3   
47029    pubity  CX6DpVTJpHD   
50530   meme.ig  CXcWFcFDU-q   
77484   meme.ig  CYti5wkBv1n   
112710  meme.ig  CXuW7-7jFEq   

                                                   legend       post_likes  \
28769   meme.igY’all gotta follow @lolpickupliness & @...     90,649 likes   
47029       pubityMade his year 🥺❤️-(Via @contentbible)3w  1,162,392 likes   
50530   mindblowin.g@MEME.IG @HOTDOGS really the best ...    228,433 likes   
77484     pubertyhit.severy boy needs to see this video4d    254,029 likes   
112710            mindblowin.gBruh 😭💀 @MEME.IG @HOTDOGS4w    754,794 likes   

                post_posted_time username  \
28769   2022-01-13T09:41:09.000Z  meme.ig   
47029   2021-12-25T13:16:12.000Z   pubity   
50530   2021-12-14T00:19:47.000Z  meme.ig   
77484   2022-01-14T13:10:12.000Z  meme.ig   
112710  2021-12-21T00:13:59.000Z  meme.ig   

                                        full_comment_data  \
28769   meme.igMy soul left my body I felt blank for a...   
47029   pubityIt is both his birthday and Christmas bt...   
50530   meme.igHomie just kept goin5w3,879 likesReplyV...   
77484   meme.igClassic fit4d2,151 likesReplyView repli...   
112710  meme.igHe’s a runner he’s a track star4w18,392...   

                                               comment  \
28769   My soul left my body I felt blank for a minute   
47029     It is both his birthday and Christmas btw 🎉🎄   
50530                             Homie just kept goin   
77484                                      Classic fit   
112710                 He’s a runner he’s a track star   

             comment_posted_time comments_likes  comment_comments_count  \
28769   2022-01-13T09:47:38.000Z      944 likes                       4   
47029   2021-12-25T13:32:15.000Z   17,624 likes                     104   
50530   2021-12-14T00:20:23.000Z    3,879 likes                       1   
77484   2022-01-14T13:11:16.000Z    2,151 likes                       2   
112710  2021-12-21T00:18:53.000Z   18,392 likes                      24   

               data_collected_time  
28769   2022-01-18 04:03:51.359886  
47029   2022-01-18 20:10:51.468783  
50530   2022-01-18 05:54:42.541059  
77484   2022-01-19 03:18:24.106187  
112710  2022-01-18 16:56:53.158904

In [78]:
df_comments.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 134465 entries, 0 to 134464
Data columns (total 12 columns):
 #   Column                  Non-Null Count   Dtype 
---  ------                  --------------   ----- 
 0   page                    134465 non-null  object
 1   postid                  134465 non-null  object
 2   legend                  134465 non-null  object
 3   post_likes              134465 non-null  object
 4   post_posted_time        134465 non-null  object
 5   username                134465 non-null  object
 6   full_comment_data       134465 non-null  object
 7   comment                 134465 non-null  object
 8   comment_posted_time     134465 non-null  object
 9   comments_likes          134465 non-null  object
 10  comment_comments_count  134465 non-null  int64 
 11  data_collected_time     134465 non-null  object
dtypes: int64(1), object(11)
memory usage: 12.3+ MB


Luckily no duplicates, some columns as likes and comment likes need to be integers, others as the dates need to me in a date format.

* There are 134.465 rows of data, meaning the same number of comments
* Post likes and comment need the numbers to be extracted and columns changed to integer 
* The three date columns don't have a correct type
* Some columns names are not explicit enough, might need to change them
* Some columns are irrelevant to this analysis. For example, the legend of the post will have no effect on the bot/non bot user so there is no point of keeping them
* No missing values! :emoji_dab:

### 1.2 Removing irrelevant columns & column names

I collected too much data, some columns are irrelevant to the analysis or the model develoment as the page, postid, post_likes and others are independant from the bots.

In [79]:
df_comments = df_comments.rename({'legend': 'caption',
                                  'comments_likes': 'comment_likes',
                                  'comment_comments_count': 'comment_reply_count'}, axis=1)

df_comments.columns

Index(['page', 'postid', 'caption', 'post_likes', 'post_posted_time',
       'username', 'full_comment_data', 'comment', 'comment_posted_time',
       'comment_likes', 'comment_reply_count', 'data_collected_time'],
      dtype='object')

In [80]:
# Dropping irrelevant columns and independant ones from the comments (for ex: number of comments)
irrelevant_columns = ["page", "postid", "caption", "full_comment_data", "post_likes", "data_collected_time", "comment_reply_count"]
df_comments = df_comments.drop(irrelevant_columns, axis=1)

# Renaming and changing the columns order
df_comments = df_comments[["username", "comment", "comment_likes", "comment_posted_time", "post_posted_time"]]

df_comments.head(1)

username                          comment comment_likes  \
0  takeajaytrip  BRUH THE BUCKS CANT MISS A SHOT   2,234 likes   

        comment_posted_time          post_posted_time  
0  2022-01-14T01:41:33.000Z  2022-01-14T01:41:02.000Z

### 1.X Changing columns types

In [81]:
# # Changing type to datetime
# df_comments['post_posted_time'] = pd.to_datetime(df_comments['post_posted_time'])
# df_comments['comment_posted_time'] = pd.to_datetime(df_comments['comment_posted_time'])
# df_comments['data_collected_time'] = pd.to_datetime(df_comments['data_collected_time'])

# # Removing non numbers characters and chaging type to int
# df_comments['post_like'] = df_comments['post_like'].str.replace('\D+', '', regex=True).astype(int)

# # Some comments have no likes and the sraper caught 'reply' instead
df_comments.loc[df_comments['comment_likes']=='Reply', 'comment_likes'] = '0 likes'
df_comments['comment_likes'] = df_comments['comment_likes'].str.replace('\D+', '', regex=True).astype(int)

### 1.2 Posted time

In [82]:
# Changing column to datetime & adding time difference
df_comments["post_posted_time"] = pd.to_datetime(df_comments["post_posted_time"])
df_comments["comment_posted_time"] = pd.to_datetime(df_comments["comment_posted_time"])

# The only useful thing I can get from the datetime columns is the time difference so I'll get it and say adios to both
df_comments["time_difference"] = (df_comments["comment_posted_time"] - df_comments["post_posted_time"]).dt.seconds
df_comments = df_comments.drop(["comment_posted_time", "post_posted_time"], axis=1)

df_comments.head()

username                                 comment  comment_likes  \
0   takeajaytrip         BRUH THE BUCKS CANT MISS A SHOT           2234   
1  reymarkable_p  Bobby Portis shooting > Steph shooting           3011   
2  jimmy_jaime94           Bucks finna have a repeat 🏆 👀            967   
3    4thgearcrew            CRAZY EYES GOT MOVES LOL 🤣🤣😭           1024   
4    __.jayriggz      Can’t wait for flights reaction 😂😂            966   

   time_difference  
0               31  
1              107  
2               95  
3              250  
4              265

In [83]:
df_comments['time_difference'].describe().round().to_frame()

time_difference
count         134465.0
mean            3293.0
std            11381.0
min                3.0
25%               70.0
50%              194.0
75%              597.0
max            86394.0

In [101]:
from plotly.subplots import make_subplots

def join_plots(plot_lst: list, row_col=None, title='', subtitle=''): 
    '''Merges multiple plotly express plots into one. 
    
    Parameters
    ----------
    plot_lst: list containing all plotly express to plot
    
    row_col: tuple indicating how many rows by columns
    '''
    if row_col == None: 
        row_col = (1, len(plot_lst))

    fig = make_subplots(rows=row_col[0], cols=row_col[1]) 

    for index, figure in enumerate(plot_lst):
        for trace in range(len(figure["data"])):
            fig.append_trace(figure["data"][trace], row=1, col=index+1)

    # if histogram is bin then 
    try:
        fig.update_traces(bingroup=None)
    except Exception:
        pass
    fig.update_layout(title=f'{title}<br><sub>{subtitle}')

    return fig

In [96]:
# Show distribution of the comments and the time difference
fig1 = px.histogram(df_comments, 
                    x = 'time_difference',
                    title = 'distribution of the time diff between the post and comment')
fig2 = px.histogram(df_comments.query('time_difference < 600'), 
                    x = 'time_difference', 
                    nbins = 1000)


sv.join_plots([fig1, fig2],
               title='Distribution of the time diff between the post and comment',
               subtitle='Right chart is filtered on less than 600 seconds')

In [111]:
fig1 = px.violin(df_comments, y="time_difference", box=True)
fig2.update_layout(yaxis_range=(0, 1000))

Most of the comment posted are 

In [86]:
fig = px.violin(df_comments, y="time_difference", box=True, # draw box plot inside the violin
                points='all', # can be 'outliers', or False
               )